<h1>Best Buy mobile Web Site Hackathon</h1>

        https://www.kaggle.com/competitions/acm-sf-chapter-hackathon-big/overview

<h1><b>Introduction</b></h1>

The intention of this project is to analyze  the data provided by the Best Buy Mobile Hackathon to predict the category/SKU based on a query presented by a user. My intentions were to create a model to predict the category, but I soon realized that this was an impossible task with the tools I had at my disposal. There was over a million categories present in the data, and even more SKUs so reduction of cardinality was extremely difficult. I tried to cluster the data to reduce the size of the dependent variable, but to cluster I needed power to run through the data which I didn’t have. I also needed to overcome other elements such as difficulties in cleaning the data, and generating more attributes that are to be engineered to improve an eventual model. Overall, the process did teach me a lot of hard lessons which I will take with me on upcoming projects.


<h1><b>Materials</b></h1>

The materials provided to me by the Hackathon was a python file to attain popular SKU, a csv containing popular SKU, a csv containing test data, a csv containing train data, and a zip file containing a couple of files. The files extracted include in the zip file will be explained below.

<b>“Product_Data” directory:</b>

categories 3MB

    An XML File containing all products

products 8.2GB

    Multiple XML files containing product data

reviews 153MB

    Multiple files containing product review data



<h2>Methodology</h2>

 My methodology starts with downloading the pertinent files from the Kaggle hackathon website and doing discovery on the files. Unzipping files was needed so I completed the unzip. I soon noticed that the files contained had an extension of .xml. This was something unfamiliar to me as we have been dealing with Xcel or CSV files. I then investigated means to convert the files within each folder to be more workable, and eventually joined them  within a consolidated file. My attempts were slow, but I then realized that I could leverage the tools provided to me in the year 2024. The tool I'm speaking of is ChatGPT, and although staying away to force myself to understand content of the degree, this was a perfect situation to start using it. Through many iterations I correctly converted all files within all the directories to csv which then led to a consolidation of all the csv files within each folder. I then uploaded these files to the file store where I worked to clean and visualize my intended results.



<p><b>The following is the purpose stated by the competion and I plan to abide by the ruleset:</b>

"Due to the internal structure of BestBuy's databases, there is no guarantee that the user clicks resulted from a search with the given query. What we do know is that the user made a query at query_time, and then, at click_time, they clicked on the sku, but we don't know that the click came from the search results. The click_time is never more than five minutes after the query_time.

In addition, there is information about products, product categories, and product reviews in product_data.tar.gz.

We have also provided a sample benchmark submission and the code that produces it. popular_skus.py is a simple python script that finds the most popular skus in each product category, and then estimates that a user clicked on one of the five most popular skus in their product category. This script produces the benchmark in popular_skus.csv.

The syntax of a submission should be the same as that in popular_skus.csv: A file with the header "sku", and each of the following lines containing the space-delimited estimates of the clicked sku that resulted after the queries in test.csv, and in the same order."</p>

<h1>Considerations</b>

It is important to consider that I did attempt to use machine learning models for feature engineering, but they did not yield objectively good results. For example I used sentiment analysis on a comment field, but the distribution of results were 99% Positive. I then used another sentiment analysis model that yielded even higher. As I investigated the results did not coinside with the content of the comment or the ultimate result of their rating. Therefore, I used rating as an indicator of sentiment which is a shame because sentiment analysis may have provided an additional feature to leverage. 

My skills in the area of Machine Learning also were lacking as I worked for 2 days to develop a model to predict a category based on user, choice_time, and query. Since the dataset had a high level of unique values in that column the amount of resources were high. Every time I tried to create a model pyspark would fail or state that there was too many unique values and needed a higher bin size for regression analysis. I plan to seek mentorship to improve on this area.

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import avg, col, coalesce, expr, unix_timestamp
from pyspark.sql.types import IntegerType
from pyspark.ml.feature import StringIndexer, OneHotEncoder
from pyspark.ml import Pipeline
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.ml.feature import VectorAssembler
from pyspark.sql.functions import unix_timestamp

# Creating spark session and importing all the needed files to consolidate.
spark = SparkSession.builder \
    .appName("Data Loading and Model Training") \
    .getOrCreate()

file_location_test="/FileStore/tables/test.csv"
file_location_train="/FileStore/tables/train.csv"
file_location_product="/FileStore/tables/Consolidated_Products.csv"
file_location_product_reviews="/FileStore/tables/Product_Review_Consolidated.csv"
file_location_product_categories="/FileStore/tables/Categories-1.csv"

file_type='csv'

infer_schema='True'
first_row_is_header='True'
delimiter=','
df_train=spark.read.format(file_type).option("infer_schema",infer_schema).option("header",first_row_is_header).option("sep",delimiter).load(file_location_train)
df_products=spark.read.format(file_type).option("infer_schema",infer_schema).option("header",first_row_is_header).option("sep",delimiter).load(file_location_product)
df_product_reviews=spark.read.format(file_type).option("infer_schema",infer_schema).option("header",first_row_is_header).option("sep",delimiter).load(file_location_product_reviews)
df_product_categories=spark.read.format(file_type).option("infer_schema",infer_schema).option("header",first_row_is_header).option("sep",delimiter).load(file_location_product_categories)

In [0]:
from pyspark.sql.functions import count
#Creating a new table with the average review scores per sku.
sku_review_result_df = df_product_reviews.fillna(3, subset=['rating']) \
    .groupby('sku') \
    .agg(avg('rating').alias('average_rating'), count('rating').alias('rating_count'))

#Creating column to investigate popularity of items clicked on on search
#sku_review_result_df = df_product_reviews.groupby('sku').agg(count('rating')).alias('query_sku_click_count')

In [0]:
#Dropping the Customer Review Average column because it is mostly empty, and the product review table will provide this context upon join
df_products=df_products.drop('customerReviewAverage')

In [0]:
from pyspark.sql.functions import col

def remove_duplicates_and_drop_nulls(df):
    # Remove duplicate records based on 'sku' column
    df = df.dropDuplicates(['sku'])
    
    # Calculate the threshold for null values
    threshold = df.count() * 0.5
    
    # Iterate over columns and drop if null values exceed 50%
    for column in df.columns:
        if df.filter(col(column).isNull()).count() > threshold:
            df = df.drop(column)
    
    return df

In [0]:
df_products_clean=remove_duplicates_and_drop_nulls(df_products)

In [0]:
joined_df=df_products_clean.join(sku_review_result_df,on="sku",how="inner")

In [0]:
df_products_clean.count()

Out[8]: 1047397

In [0]:
df_products.count()

Out[9]: 1537869

In [0]:
#Dropping any column that has over 50% null values
bad_columns=[]
for column in joined_df.columns:
        if joined_df.filter(col(column).isNull()).count() > .5:
            bad_columns.append(column)
for col in bad_columns:
    joined_df.drop(col)

In [0]:
len(joined_df.columns)

Out[11]: 45

In [0]:
from pyspark.sql.functions import col, unix_timestamp, from_unixtime
# Assuming you have a DataFrame named df_train
# Register the DataFrame as a temporary view
df_train.createOrReplaceTempView("train")

# Cast click_time and query_time columns to timestamp
df_train = df_train.withColumn("click_time", from_unixtime(unix_timestamp(col("click_time"), "yyyy-MM-dd HH:mm:ss.SSS")))
df_train = df_train.withColumn("query_time", from_unixtime(unix_timestamp(col("query_time"), "yyyy-MM-dd HH:mm:ss.SSS")))

# Calculate time difference in seconds
time_diff_seconds = (unix_timestamp(col("click_time")) - unix_timestamp(col("query_time")))

# Convert time difference to minutes
time_diff_minutes = time_diff_seconds / 60

# Add time difference in minutes as a new column
df_train = df_train.withColumn("choice_time_minutes", time_diff_minutes)

# Show the DataFrame
df_train.show()

# Don't forget to stop the SparkSession when you're done


+--------------------+-------+------------------+--------------------+-------------------+-------------------+-------------------+
|                user|    sku|          category|               query|         click_time|         query_time|choice_time_minutes|
+--------------------+-------+------------------+--------------------+-------------------+-------------------+-------------------+
|000000df17cd56a5d...|2125233|      abcat0101001|Televisiones Pana...|2011-09-01 23:44:52|2011-09-01 23:43:59| 0.8833333333333333|
|000001928162247ff...|2009324|      abcat0101001|               Sharp|2011-09-05 12:25:37|2011-09-05 12:25:01|                0.6|
|000017f79c2b5da56...|1517163|pcmcat193100050014|                nook|2011-08-24 12:56:58|2011-08-24 12:55:13|               1.75|
|000017f79c2b5da56...|2877125|      abcat0101001|                 rca|2011-10-25 07:18:14|2011-10-25 07:16:51| 1.3833333333333333|
|000017f79c2b5da56...|2877134|      abcat0101005|                 rca|2011-10-25 07

In [0]:
final_joined_df=joined_df.join(df_train, on='sku',how='inner')

In [0]:
df_product_categories=df_product_categories.withColumnRenamed('name','category_name')
df_product_categories = df_product_categories.dropDuplicates(['category'])

In [0]:
final_joined_df_cat=final_joined_df.join(df_product_categories, on='category',how='inner')

Below I went ahead and cleaned up the data types, dropped unnecessary columns, and renamed a few to better describe the content.

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import to_date, to_timestamp, date_format
from pyspark.sql.types import FloatType

# Assuming spark is your SparkSession and final_joined_df_cat is your DataFrame

# Convert startDate and priceUpdateDate to date type
final_joined_df_cat = final_joined_df_cat.withColumn("startDate", to_date("startDate")) \
                                         .withColumn("priceUpdateDate", to_date("priceUpdateDate"))

# Convert regularPrice and salePrice to float type
final_joined_df_cat = final_joined_df_cat.withColumn("regularPrice", final_joined_df_cat["regularPrice"].cast(FloatType())) \
                                         .withColumn("salePrice", final_joined_df_cat["salePrice"].cast(FloatType()))

# Convert click_time and query_time to time format
final_joined_df_cat = final_joined_df_cat.withColumn("click_time", date_format(to_timestamp("click_time", "hh:mm:ss a"), "hh:mm:ss a")) \
                                         .withColumn("query_time", date_format(to_timestamp("query_time", "hh:mm:ss a"), "hh:mm:ss a"))

# Drop column 'id2' and 'id4'
final_joined_df_cat = final_joined_df_cat.drop('id2')
final_joined_df_cat = final_joined_df_cat.drop('id4')

# Rename columns 'name3' and 'name5'
final_joined_df_cat = final_joined_df_cat.withColumnRenamed('name3', 'SubCategory') \
                                         .withColumnRenamed('name5', 'SubCategory2')


In [0]:
#from pyspark.sql.functions import col, unix_timestamp

# Calculate time difference in seconds
#time_diff_seconds = (unix_timestamp(col("click_time"), "hh:mm:ss a") - 
                     #unix_timestamp(col("query_time"), "hh:mm:ss a"))

# Convert time difference to minutes and cast to integer
#time_diff_minutes = (time_diff_seconds / 60).cast("int")

# Add time difference in minutes as a new column
#final_joined_df_cat = final_joined_df_cat.withColumn("choice_time_minutes", time_diff_minutes)

# Show the DataFrame
#final_joined_df_cat.show()


  File <command-2222413741197440>:5
    unix_timestamp(col("query_time"), "hh:mm:ss a"))
    ^
IndentationError: unexpected indent


In [0]:
final_joined_df_cat.count()

Out[18]: 868120

In [0]:
final_joined_df_cat.filter(col('choice_time_minutes').isNull()).count()

Out[19]: 1760

In [0]:
#final_joined_df_cat = final_joined_df_cat.na.drop(subset=['choice_time_minutes'])

# Delete records with null values in the specified column
#final_joined_df_cat = final_joined_df_cat.filter(final_joined_df_cat["choice_time_minutes"].isNotNull())

In [0]:
final_joined_df_cat.display()

category sku productId name source type startDate new active activeUpdateDate regularPrice salePrice onSale advertisedPriceRestriction restrictedSalePrice priceUpdateDate digital preowned upc id name2 format freeShipping inStoreAvailability inStoreAvailabilityText inStoreAvailabilityTextHtml inStoreAvailabilityUpdateDate itemUpdateDate onlineAvailability onlineAvailabilityText onlineAvailabilityTextHtml onlineAvailabilityUpdateDate releaseDate specialOrder class classId subclass subclassId department departmentId bestBuyItemId image thumbnailImage marketplace average_rating rating_count user query click_time query_time choice_time_minutes category_name SubCategory SubCategory2 pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB Cable bestbuy HardGood null 0 1 2012-07-02T22:49:14 14.99 14.99 0 0 14.99 2010-05-18 0 0 null null null null null null null null null null null null null null null null null null null null null null null null null null 2.3636363636363638 11 03786fb9c63eb6f30c96626df054d3ecc32fd5da cable null null 0.31666666666666665 USB Chargers Best Buy null pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB Cable bestbuy HardGood null 0 1 2012-07-02T22:49:14 14.99 14.99 0 0 14.99 2010-05-18 0 0 null null null null null null null null null null null null null null null null null null null null null null null null null null 2.3636363636363638 11 0416058523834600c0ca69b574e01d06eb889c42 usb cable null null 0.6833333333333333 USB Chargers Best Buy null pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB Cable bestbuy HardGood null 0 1 2012-07-02T22:49:14 14.99 14.99 0 0 14.99 2010-05-18 0 0 null null null null null null null null null null null null null null null null null null null null null null null null null null 2.3636363636363638 11 076b69a3c3da468b33c10fb0aca48306e3d6d09f usb cable null null 1.1833333333333333 USB Chargers Best Buy null pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB Cable bestbuy HardGood null 0 1 2012-07-02T22:49:14 14.99 14.99 0 0 14.99 2010-05-18 0 0 null null null null null null null null null null null null null null null null null null null null null null null null null null 2.3636363636363638 11 0bc0971d44c0eb913c1865c3595b1891ebc8017e USB wire null null 0.35 USB Chargers Best Buy null pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB Cable bestbuy HardGood null 0 1 2012-07-02T22:49:14 14.99 14.99 0 0 14.99 2010-05-18 0 0 null null null null null null null null null null null null null null null null null null null null null null null null null null 2.3636363636363638 11 0e8a5f5b06a973b0f1a1b7d48ed18a4dfa1bcf47 usb cable null null 1.0333333333333334 USB Chargers Best Buy null pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB Cable bestbuy HardGood null 0 1 2012-07-02T22:49:14 14.99 14.99 0 0 14.99 2010-05-18 0 0 null null null null null null null null null null null null null null null null null null null null null null null null null null 2.3636363636363638 11 106fe03e18ddd12061c23a2fdfd158248a5680ca Android hdmi cable null null 0.38333333333333336 USB Chargers Best Buy null pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB Cable bestbuy HardGood null 0 1 2012-07-02T22:49:14 14.99 14.99 0 0 14.99 2010-05-18 0 0 null null null null null null null null null null null null null null null null null null null null null null null null null null 2.3636363636363638 11 19e1f9181d39788061fd02577de7a1d59ef6b8b2 html adaptor cable null null 1.7 USB Chargers Best Buy null pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB Cable bestbuy HardGood null 0 1 2012-07-02T22:49:14 14.99 14.99 0 0 14.99 2010-05-18 0 0 null null null null null null null null null null null null null null null null null null null null null null null null null null 2.3636363636363638 11 1aa5d2c3bbaa9e1ffccabe69ffa9428241a54c93 5.1 speake null null 3.6 USB Chargers Best Buy null pcmcat171900050026 1000247 1.21821E+12 Rocketfish™ - 1.5' USB 

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

<h1>Conclusion</h1>

In conclusion the visualization is a representative sample, but you can see the sample yielded faster clicks depending on rating. This leads me to believe the higher the satisfaction of the product the faster someone is likely to choose it. This is important information when creating a model for prediction as we can train the model in speed of click, and average rating among other attributes we have yet to discover. I can see there is high variation of ratings in categories like lens filters using a box plot and see some work needing to be done on tv wall mount rating. The wall mounts seem to have high engagement, but lower rating than expected. If I had the capabilities to create a machine learning model to predict a category/SKU depending on some key factors, I would do so, but my attempts to create one have failed. 


In [0]:
#Creating a view to run SQL Queries
#final_joined_df_cat.createOrReplaceTempView("Final_DF")
#display(spark.sql(
    #"SELECT * FROM Final_DF "
    #).toPandas())

In [0]:
final_joined_df_cat.count()

Out[21]: 868120